In [1]:
import pandas as pd
import torch
import numpy as np
from transformers import BertTokenizer, BertModel
from torch import nn
from torch.optim import Adam
from tqdm import tqdm
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
import csv
from sklearn.utils import shuffle
import tensorflow as tf
import pandas as pd
import torch
import numpy as np
from transformers import BertTokenizer, BertModel , AutoModel
from torch import nn
from torch.optim import Adam
from tqdm import tqdm
import os 
import string 
import glob
import joblib
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize 
from nltk.corpus import stopwords

In [2]:
def createDataset(path, path_texts):
    train_label_path = path + "summary.tsv"
    df_train_label = pd.read_csv(train_label_path, delimiter="\t")
    txt_files = glob.glob(path_texts)
    txt_files.sort()
    data = []
    for files in txt_files:
        with open(files) as content:
            i=0
            for item in content:
                if i == 0:
                    interm = item
                    i = i+1
                else:
                    interm= interm + item
                    i= i+1
            data.append(interm)

    dataframe = {'content': data,
                'label': df_train_label['label']
                }

    frenchds = pd.DataFrame(dataframe)
    frenchds['label']= frenchds['label'].apply(lambda x:'satire' if x==1 else 'nonSatire')
    frenchds['content'] = frenchds['content'].apply(lambda x: x.translate(str.maketrans('', '', string.punctuation)))
    frenchds['content'] = frenchds['content'].replace("\\n", "")
    return frenchds

In [31]:
device = torch.device('cpu') 
data_path_train   = '/Users/catalina.chirita/Desktop/Disertatie/FrenchSatireDataset/train/'
texts_path_train = "/Users/catalina.chirita/Desktop/Disertatie/FrenchSatireDataset/train/texts/*.txt"

data_path_test   = '/Users/catalina.chirita/Desktop/Disertatie/FrenchSatireDataset/test/'
texts_path_test = "/Users/catalina.chirita/Desktop/Disertatie/FrenchSatireDataset/test/texts/*.txt"

train_dataset = createDataset(data_path_train,texts_path_train)
test_dataset=createDataset(data_path_test,texts_path_test)

def remove_punctuation(text):
    punctuationfree="".join([i for i in text if i not in string.punctuation])
    return punctuationfree
#storing the puntuation free text
train_dataset['content']= train_dataset['content'].apply(lambda x:remove_punctuation(x))
train_dataset['content']= train_dataset['content'].apply(lambda x: x.lower())

test_dataset['content']= test_dataset['content'].apply(lambda x:remove_punctuation(x))
test_dataset['content']= test_dataset['content'].apply(lambda x: x.lower())


train_dataset['content']= train_dataset['content'].apply(lambda x: word_tokenize(x))
test_dataset['content']= test_dataset['content'].apply(lambda x: word_tokenize(x))

final_stopwords_list = stopwords.words('french')
final_stopwords_list.append('«')
final_stopwords_list.append('»')
final_stopwords_list.append('’')
final_stopwords_list.append('-')
def remove_stopwords(text):
    output= [i for i in text if i not in final_stopwords_list]
    return output
def remove_digit(text):
    output= [c for c in text if not c.isdigit()]
    return output

train_dataset['content']= train_dataset['content'].apply(lambda x:remove_stopwords(x))
train_dataset['content']= train_dataset['content'].apply(lambda x:remove_digit(x))

test_dataset['content']= test_dataset['content'].apply(lambda x:remove_stopwords(x))
test_dataset['content']= test_dataset['content'].apply(lambda x:remove_digit(x))

for array in range(len(train_dataset["content"])):
    train_dataset["content"][array]=' '.join(train_dataset["content"][array]) 
    
for array in range(len(test_dataset["content"])):
    test_dataset["content"][array]=' '.join(test_dataset["content"][array]) 

In [19]:
train_dataset['content'][0][:512]

'mystère disparition chat mère michel captive passionne france troisième volet enquête exclusive troisième volet enquête disparition chat mère michel après avoir étudié faits contradictions témoignages penchonsnous cas étrange père lustucru secrets première fois révélés plus trois semaines écoulées depuis disparition chat mère michel recherches canton cours eau donnent aucun résultat gendarmerie tente comprendre emploi temps mère michel tandis apparaît peu plus chaque jour comme principal suspect père lustuc'

In [29]:
print(len(test_dataset["content"]))
print(type(train_dataset["content"]))

2854
<class 'pandas.core.series.Series'>


In [21]:
train_dataset["content"][0]

'mystère disparition chat mère michel captive passionne france troisième volet enquête exclusive troisième volet enquête disparition chat mère michel après avoir étudié faits contradictions témoignages penchonsnous cas étrange père lustucru secrets première fois révélés plus trois semaines écoulées depuis disparition chat mère michel recherches canton cours eau donnent aucun résultat gendarmerie tente comprendre emploi temps mère michel tandis apparaît peu plus chaque jour comme principal suspect père lustucru enchaîne témoignages contradictoires si premier temps affirmait avoir discuté mère michel affirme ensuite avoir italie moment faits mesure apporter vision nouvelle passé père lustucru regard nouvelles informations exclusives nombreux commentateurs époque passé père lustucru durant guerre plus trouble si libération père lustucru vanté avoir monté réseau résistance arrièrepays creil personne pays a souvenir retrouvé témoins affirment lustucru parti allemagne devançant ordre service

In [22]:
from transformers import pipeline
src = "fr"
dst = "en"

task_name = f"translation_{src}_to_{dst}"
model_name = f"Helsinki-NLP/opus-mt-{src}-{dst}"
translator = pipeline(task_name, model=model_name, tokenizer=model_name,max_length = 512, truncation=True)
for array in range(len(train_dataset["content"])):
    print(array)
    translate = translator(train_dataset["content"][array][:512])
    train_dataset["content"][array]=list(translate[0].values())
    print(train_dataset["content"][array])
    
for array in range(len(test_dataset["content"])):
    print(array)
    translate = translator(test_dataset["content"][array][:512])
    test_dataset["content"][array]=list(translate[0].values())
    print(test_dataset["content"][array])

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


Downloading:   0%|          | 0.00/1.38k [00:00<?, ?B/s]

0
['mystery disappearance cat mother michel captive passionne france third part exclusive investigation third part investigation disappearance cat mother michel after studying facts contradictions testimonials pend us strange case father lustucru secrets first time revealed plus three weeks last since disappeared cat mother michel searches canton courtyard water give no result gendarmerie attempt to understand job time mother michel while appears little more every day as main suspect father lustuc']
1
['every week gorafi returns investigation missing cat mother michel light up case under light new disappearance cat mother michel contradictions heart testimonials cat mother michel disappears day February quickly investigators find differences testimonials main actors made after phone call gendarmerie creil see first part investigation yesterday father lustucru became first suspect man said ready to provide all necessary help find cat mother michel so announcement disappearance still mad

['handle – famous mont saint michel will temporarily leave bay several months pattern many repairs preview heavily corroded hull damaged after several storms winter immobilization should last between months met anger local authorities tourists born idea george pompidou dreamed large ship wide normandy built valery giscard estaing inaugurated françois mitterrand mont saint michel is part integral heritage handle silhouette time decried is part of national heritage even my']
18
['new canine scandal michèle delaunay this minister great rival alain juppé municipal race found under fire news after dog accused of biting two policemen a week languages untied last days reveal several ten thousand other victims new canine scandal michèle delaunay this minister great rival alain juppé municipal race found under fire news after dog accused of biting two policemen a week languages untied dernie']
19
['aleppo – Syrian rebels announced evening have totally lost faith credible support france face reg

['symbol extinguished yesterday domicile rueilmalmaison kevin duchard years deceased suites long illness first bear name millions other boys would adopt some time later launcher mode precursor also young deep man humility person loved French also guide other disappears today part we fly to heaven comments this other kevin years kevin duchard before all that traced path born February kevin duchard very quickly inspired other parents decided also call son kevin']
35
['Everyone knows name no one has ever seen face to exception prisoners who is responsible for joel suspended probation not particular for almost years charged with helping detainees French execution sentence psychological follow-up social sometimes just practical worth nickname best friend prisoner mission tries to accomplish better possible despite more problems more everyone knows name no one has ever seen face to exception prisoners whose charge joel suspended agent probation not particular for soon years c']
36
['history 

...

['want to give again feeling if repars cest because jy crois nicolas hulot has announced Tuesday resign post minister transition ecological solidarity without having warned the executive beforehand is this started reducing the use pesticides answer no is it started halting the erosion biodiversity answer no is it started putting situation to stop lartificalization soils answer no declared preamble nicolas hulot micro france inter then questioned maintenance government non lman announced to take first']
2772
['emmanuel macron made Monday surprise visit local of an association occupant citizenship accompaniment families evry lessonne great suburb of Paris where to participate late afternoon fifth public debate indicated lelysée first travel suburb framework great debate head letat has to exchange from hours approximately elected representatives of associations franciliens evrycourcourcouronnes common inhabitants located thirty kilometers south paris visit surprise emmanuel macron customa

['president lunion Independent democrats udi jeanchristophe lagarde said Wednesday prefer tiki without papers two brothers kouachi papers subject resignation stéphane tiki expresident young popular has residence permit nest someone disembarks france clandestine way nightly truck has demonstrated that it perfectly integrated has estimated jeanchristophe lagarde Wednesday the show questions dinfo lcpfrance infole mondiafp recalling if it asks before French years according to this show systematism right strong na lie']
2789
['l stop treatments vincent lambert patient tetraplegic vegetative state for more years nest assassination has judged Wednesday cnews interim president republican jean leonetti father law governing fine life doctor vincent lambert become symbol debate end life france has engaged Tuesday new stop treatments rendered possible Friday court cassation jean leonetti doctors reason this story absolute human drama emphasizes jean leonetti himself cardiologist to torn family to

['secretary general lr bernard accoyer has estimated Sunday antenna party need for a powerful renewal to which will work next months until the election of a new president conception must be political party today review all launched announcing having asked very young intellectuals already to think about it the former president the national assembly considers parties faced acute crisis political parties if they bad reputation useful moreover include constitution as indispensable actors']
2806
['businessman ziad takieddine central character the case karachi arrested Monday London while he was about to take train home bets despite ban leaving French territory aton learned Tuesday judicial source confirming information rtl businessman Francolibanese obtained December recover for days passport only return Senegal has specified judicial source arrested station saintpancras London should be introduced Tuesday investigating judge renaud van ruymbeke could refer judge li']
2807
['second round ma

['jeanlouis debré certainly had to reserve president constitutional council held to say Monday evening lelysée that he considered worrying attempts circumvention decisions government parliament at ceremony vows françois hollande high court of course natural conforming the spirit ve republic that following a censorship government parliament can seek to reach the objective that they had set other ways observed jeanlouis debré evoking very high income tax censored then reviewed government so that']
2823
['axe war less provisionally buried between europe ecologies green government certain many those parties ndlr ideas speech françois hollande sest jolly national secretary eelv pascal durand Friday bfmtv head lettat expressed before second environmental conference considered president priority energy transition made great law energy transition voted before end it is very important also stressed obviously will budder pleasure elsewhere said to have received sms prem']
2824
['crisis redundanc

['strong participation has great surprise European elections much French but abstaining near a voter two be precise how distribute this forbearance territory discover thanks interactive map below click department choice more dark color less voters participated some rural departments especially those origin movement yellow vests much more voted this year in last elections renewed mobilization however asks question differences voting according to type territo']
2840
['find video all political chronicles first danna cabana click here Monday afternoon hours nicolas sarkozy will participate office political extraordinary seat mp real false return great return nicolas sarkozy wants above all talk great return great return it would mean return good or consider moment it is hardly fourteen months has beaten françois hollande still quite desired then above all come back now it would mean returning negative note since return cause decision council consti']
2841
['subject has widely debated Wedne

In [9]:
#258,485.921 , 7859,7858

In [48]:
train_dataset.head()

content   label
0  mystère disparition chat mère michel captive p...  satire
1  toute semaine gorafi revient enquête dispariti...  satire
2  montauban – habitant montauban a vécu mésavent...  satire
3  fallu plus ans treize longues années vérité fa...  satire
4  cela fait partie petites histoires égayent jou...  satire

In [49]:
test_dataset.head()

content   label
0  [Hello circumspect doctor little chamomile yea...  satire
1  [sydney rare genetic diseases of which media r...  satire
2  [4th Directive on driving permits p2a double s...  satire
3  [Hello doctor little elise call commonly gifte...  satire
4  [has sold more jk rowling harry potter known a...  satire

In [2]:
#train_dataset.to_pickle("francetranslatetoromanian.pkl")
#test_dataset.to_pickle("testfrancetranslatetoromanian.pkl")

train_dataset = pd.read_pickle("francetranslatetoromanian.pkl")
# print(train_dataset)

test_dataset = pd.read_pickle("testfrancetranslatetoromanian.pkl")
print(test_dataset)

                                                content      label
0     [Hello circumspect doctor little chamomile yea...     satire
1     [sydney rare genetic diseases of which media r...     satire
2     [4th Directive on driving permits p2a double s...     satire
3     [Hello doctor little elise call commonly gifte...     satire
4     [has sold more jk rowling harry potter known a...     satire
...                                                 ...        ...
2849  [invited Wednesday morning bfmtv alexis corbiè...  nonSatire
2850  [point mayors elected from the first round mun...  nonSatire
2851  [this consoleracy non companion girl na took p...  nonSatire
2852  [europe ecologies Greens achieved perfect coup...  nonSatire
2853  [heart debate easily caricatural question abol...  nonSatire

[2854 rows x 2 columns]


In [3]:
np.random.seed(112)
df_train, df_val, df_test = np.split(train_dataset.sample(frac=1, random_state=42), 
                                     [int(.8*len(train_dataset)), int(.9*len(train_dataset))])

print(len(df_train),len(df_val), len(df_test))

6972 872 872


In [3]:
class BertClassifier(nn.Module):

    def __init__(self, dropout=0.5):

        super(BertClassifier, self).__init__()

        self.bert = AutoModel.from_pretrained('bert-base-cased')
        self.dropout = nn.Dropout(dropout)
        self.linear = nn.Linear(768, 2)
        self.relu = nn.ReLU()

    def forward(self, input_id, mask):

        _, pooled_output = self.bert(input_ids= input_id, attention_mask=mask,return_dict=False)
        dropout_output = self.dropout(pooled_output)
        linear_output = self.linear(dropout_output)
        final_layer = self.relu(linear_output)
        return final_layer , pooled_output

In [4]:
from transformers import AutoTokenizer, AutoModel
import torch
# load tokenizer and model
tokenizer = AutoTokenizer.from_pretrained('bert-base-cased')

labels = {'nonSatire':0,
          'satire':1
          }

class Dataset(torch.utils.data.Dataset):

    def __init__(self, df):

        self.labels = [labels[label] for label in df['label']]
        self.texts = [tokenizer(text, 
                               padding='max_length', max_length = 512, truncation=True,
                                return_tensors="pt") for text in df['content']]

    def classes(self):
        return self.labels

    def __len__(self):
        return len(self.labels)

    def get_batch_labels(self, idx):
        # Fetch a batch of labels
        return np.array(self.labels[idx])

    def get_batch_texts(self, idx):
        # Fetch a batch of inputs
        return self.texts[idx]

    def __getitem__(self, idx):

        batch_texts = self.get_batch_texts(idx)
        batch_y = self.get_batch_labels(idx)

        return batch_texts, batch_y
    

In [6]:
def train(model, train_data, val_data, learning_rate, epochs):

    train, val = Dataset(train_data), Dataset(val_data)

    train_dataloader = torch.utils.data.DataLoader(train, batch_size=2, shuffle=True)
    val_dataloader = torch.utils.data.DataLoader(val, batch_size=2)

    use_cuda = torch.cuda.is_available()
    device = torch.device("cuda" if use_cuda else "cpu")

    criterion = nn.CrossEntropyLoss()
    optimizer = Adam(model.parameters(), lr= learning_rate)

    if use_cuda:

            model = model.cuda()
            criterion = criterion.cuda()

    for epoch_num in range(epochs):

            total_acc_train = 0
            total_loss_train = 0

            for train_input, train_label in tqdm(train_dataloader):

                train_label = train_label.to(device)
                mask = train_input['attention_mask'].to(device)
                input_id = train_input['input_ids'].squeeze(1).to(device)

                output = model(input_id, mask)
                
                batch_loss = criterion(output, train_label)
                total_loss_train += batch_loss.item()
                
                acc = (output.argmax(dim=1) == train_label).sum().item()
                total_acc_train += acc

                model.zero_grad()
                batch_loss.backward()
                optimizer.step()
            
            total_acc_val = 0
            total_loss_val = 0

            with torch.no_grad():

                for val_input, val_label in val_dataloader:

                    val_label = val_label.to(device)
                    mask = val_input['attention_mask'].to(device)
                    input_id = val_input['input_ids'].squeeze(1).to(device)

                    output = model(input_id, mask)

                    batch_loss = criterion(output, val_label)
                    total_loss_val += batch_loss.item()
                    
                    acc = (output.argmax(dim=1) == val_label).sum().item()
                    total_acc_val += acc
            
            print(
                f'Epochs: {epoch_num + 1} | Train Loss: {total_loss_train / len(train_data): .3f} | Train Accuracy: {total_acc_train / len(train_data): .3f} | Val Loss: {total_loss_val / len(val_data): .3f} | Val Accuracy: {total_acc_val / len(val_data): .3f}')
                  

In [7]:
EPOCHS = 5
model = BertClassifier()
LR = 1e-6
              
train(model, df_train, df_val, LR, EPOCHS)

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertModel: ['cls.predictions.decoder.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
  0%|          | 0/3486 [00:00<?, ?it/s]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


100%|██████████| 3486/3486 [22:21:15<00:00, 23.09s/it]     


Epochs: 1 | Train Loss:  0.255 | Train Accuracy:  0.699 | Val Loss:  0.116 | Val Accuracy:  0.909


100%|██████████| 3486/3486 [7:19:16<00:00,  7.56s/it]  


...

Epochs: 3 | Train Loss:  0.030 | Train Accuracy:  0.982 | Val Loss:  0.044 | Val Accuracy:  0.971


100%|██████████| 3486/3486 [7:15:55<00:00,  7.50s/it]  


Epochs: 4 | Train Loss:  0.013 | Train Accuracy:  0.993 | Val Loss:  0.042 | Val Accuracy:  0.975


100%|██████████| 3486/3486 [16:58:35<00:00, 17.53s/it]       


Epochs: 5 | Train Loss:  0.006 | Train Accuracy:  0.997 | Val Loss:  0.039 | Val Accuracy:  0.977


In [8]:
# Save Model Using joblib
import pandas
from sklearn import model_selection
from sklearn.linear_model import LogisticRegression
import joblib

filename = 'finalized_model_frenchtoenglish.sav'
joblib.dump(model, filename)

['finalized_model_frenchtoenglish.sav']

In [10]:
evaluate(model, df_test)

Test Accuracy:  0.971


In [7]:
test_dataset1 = pd.read_pickle("testfrancetranslatetoromanian.pkl")
print(test_dataset1)

filename = 'finalized_model_frenchtoenglish.sav'
loaded_model1 = joblib.load(filename)

                                                content      label
0     [Hello circumspect doctor little chamomile yea...     satire
1     [sydney rare genetic diseases of which media r...     satire
2     [4th Directive on driving permits p2a double s...     satire
3     [Hello doctor little elise call commonly gifte...     satire
4     [has sold more jk rowling harry potter known a...     satire
...                                                 ...        ...
2849  [invited Wednesday morning bfmtv alexis corbiè...  nonSatire
2850  [point mayors elected from the first round mun...  nonSatire
2851  [this consoleracy non companion girl na took p...  nonSatire
2852  [europe ecologies Greens achieved perfect coup...  nonSatire
2853  [heart debate easily caricatural question abol...  nonSatire

[2854 rows x 2 columns]


In [8]:
from sklearn.ensemble import VotingClassifier
import pandas as pd
    
def evaluate2models2(model,test_dataset):

    test = Dataset(test_dataset)

    test_dataloader = torch.utils.data.DataLoader(test, batch_size=1)

    use_cuda = torch.cuda.is_available()
    device = torch.device("cuda" if use_cuda else "cpu")

    if use_cuda:

        model = model.cuda()

    total_acc_test = 0
    dataframe_val = []
    dataframe_wght = []
    dataframe_satire=[]
    dataframe_label = []
    dataframe_cls =[]
    pooled_output_dat = []
    with torch.no_grad():

    
        for test_input, test_label in test_dataloader:

                test_label = test_label.to(device)
                mask = test_input['attention_mask'].to(device)
                input_id = test_input['input_ids'].squeeze(1).to(device)

                output = model(input_id, mask)
                pooled_output = output[1]
                
                acc = (output[0].argmax(dim=1) == test_label).sum().item()
                if acc == 1:
                    if output[0].argmax(dim=1)[0] == 1:
                        dataframe_satire.append('satire')
                        print('satire')
                    else:
                        dataframe_satire.append('nonSatire')
                        print('nonSatire')
                else:
                    dataframe_satire.append('error')
                    print('error of preddiction')
                    
                pooled_output = pooled_output.tolist()
                pooled_output_dat.append(pooled_output)
                output = output[0].tolist()  
                test_label = test_label.tolist()
                dataframe_val.append(output[0])
                dataframe_wght.append(float(0.40))
                dataframe_label.append(test_label[0])
                total_acc_test += acc
    
        model_dataset = {'Value':dataframe_val ,
        'Weight': dataframe_wght,
        'Label': dataframe_label,
        'Type': dataframe_satire}
        
        model_dataset = pd.DataFrame(model_dataset)
        model_dataset.to_pickle("dataframefr-eng2.pkl")
        
        model_d = {'Pooled output france-eng':pooled_output_dat}
 
        model_dataset2 = pd.DataFrame(model_d)
        model_dataset2.to_pickle("dataframefr_eng_pldout.pkl")
        
        print("Model1 DF", model_dataset)
        print(f'Test Accuracy model: {total_acc_test / len(test_dataset): .3f}')

In [9]:
evaluate2models2(loaded_model1,test_dataset1)

satire
satire
satire
satire
satire
satire
error of preddiction
satire
satire
satire
error of preddiction
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
error of preddiction
satire
satire
satire
error of preddiction
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
error of preddiction
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
error of preddiction
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
error of preddiction
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
satire
error of preddiction
error of preddiction
error of preddiction
satire
satire
satire

satire
error of preddiction
error of preddiction
satire
error of preddiction
error of preddiction
error of preddiction
error of preddiction
satire
error of preddiction
error of preddiction
error of preddiction
satire
error of preddiction
error of preddiction
satire
error of preddiction
error of preddiction
error of preddiction
error of preddiction
satire
satire
error of preddiction
error of preddiction
satire
error of preddiction
satire
error of preddiction
satire
error of preddiction
error of preddiction
error of preddiction
satire
satire
error of preddiction
satire
satire
satire
satire
satire
satire
satire
error of preddiction
error of preddiction
error of preddiction
error of preddiction
error of preddiction
error of preddiction
error of preddiction
satire
error of preddiction
satire
satire
error of preddiction
error of preddiction
satire
error of preddiction
error of preddiction
error of preddiction
error of preddiction
satire
error of preddiction
error of preddiction
error of pred

error of preddiction
error of preddiction
satire
error of preddiction
error of preddiction
error of preddiction
error of preddiction
error of preddiction
error of preddiction
error of preddiction
error of preddiction
satire
satire
satire
satire
satire
satire
error of preddiction
satire
satire
error of preddiction
satire
satire
satire
satire
error of preddiction
satire
satire
satire
satire
satire
satire
satire
satire
error of preddiction
error of preddiction
satire
error of preddiction
satire
satire
satire
error of preddiction
satire
satire
satire
satire
satire
error of preddiction
error of preddiction
satire
satire
satire
error of preddiction
satire
error of preddiction
satire
satire
satire
error of preddiction
satire
satire
satire
satire
satire
satire
satire
error of preddiction
satire
satire
satire
error of preddiction
satire
error of preddiction
satire
satire
error of preddiction
error of preddiction
error of preddiction
satire
satire
satire
error of preddiction
nonSatire
nonSatire


nonSatire
nonSatire
nonSatire
nonSatire
error of preddiction
error of preddiction
nonSatire
nonSatire
nonSatire
nonSatire
nonSatire
nonSatire
nonSatire
nonSatire
error of preddiction
nonSatire
nonSatire
nonSatire
nonSatire
error of preddiction
nonSatire
error of preddiction
nonSatire
nonSatire
error of preddiction
nonSatire
nonSatire
nonSatire
nonSatire
nonSatire
nonSatire
error of preddiction
nonSatire
nonSatire
nonSatire
error of preddiction
nonSatire
error of preddiction
nonSatire
nonSatire
nonSatire
error of preddiction
error of preddiction
nonSatire
nonSatire
nonSatire
error of preddiction
error of preddiction
nonSatire
error of preddiction
nonSatire
error of preddiction
nonSatire
nonSatire
nonSatire
error of preddiction
error of preddiction
nonSatire
nonSatire
nonSatire
error of preddiction
error of preddiction
error of preddiction
nonSatire
nonSatire
nonSatire
nonSatire
error of preddiction
error of preddiction
error of preddiction
nonSatire
nonSatire
nonSatire
nonSatire
error o

nonSatire
nonSatire
nonSatire
error of preddiction
error of preddiction
error of preddiction
nonSatire
nonSatire
error of preddiction
error of preddiction
nonSatire
error of preddiction
nonSatire
nonSatire
nonSatire
error of preddiction
nonSatire
nonSatire
nonSatire
nonSatire
error of preddiction
nonSatire
error of preddiction
nonSatire
nonSatire
error of preddiction
nonSatire
error of preddiction
error of preddiction
error of preddiction
nonSatire
nonSatire
nonSatire
nonSatire
error of preddiction
nonSatire
error of preddiction
nonSatire
error of preddiction
nonSatire
nonSatire
nonSatire
error of preddiction
error of preddiction
nonSatire
nonSatire
error of preddiction
nonSatire
nonSatire
nonSatire
nonSatire
nonSatire
nonSatire
nonSatire
error of preddiction
nonSatire
error of preddiction
nonSatire
nonSatire
error of preddiction
nonSatire
nonSatire
nonSatire
error of preddiction
nonSatire
nonSatire
nonSatire
error of preddiction
nonSatire
nonSatire
nonSatire
nonSatire
nonSatire
error 